In [1]:
import pandas as pd
from astropy.coordinates import SkyCoord
from astropy import units as u
import numpy as np

from bokeh.plotting import output_notebook, figure, show
from bokeh.models.ranges import Range1d
from bokeh.models import HoverTool, tools,ColumnDataSource, Whisker, ColorBar, LinearColorMapper
output_notebook()

Loading BokehJS ...

In [2]:
names =['x',
        'y',
        'f275w_mag',
        'f275w_rms',
        'f275w_qf',
        'f275w_shap',
        'f275w_numexp',
        'f275w_numwellmeasure',
        'f336w_mag',
        'f336w_rms',
        'f336w_qf',
        'f336w_shap',
        'f336w_numexp',
        'f336w_numwellmeasure',
        'f435w_mag',
        'f435w_rms',
        'f435w_qf',
        'f435w_shap',
        'f435w_numexp',
        'f435w_numwellmeasure',
        'f606w_mag',
        'f606w_rms',
        'f606w_qf',
        'f606w_shap',
        'f606w_numexp',
        'f606w_numwellmeasure',
        'f814w_mag',
        'f814w_rms',
        'f814w_qf',
        'f814w_shap',
        'f814w_numexp',
        'f814w_numwellmeasure',
        'member_prob',
        'ra',
        'dec',
        'star_id',
        'iter_found'
]

In [3]:
data=pd.read_csv('hlsp_hugs_hst_wfc3-uvis-acs-wfc_ngc0104_multi_v1_catalog-meth3.txt'
                 ,delim_whitespace=True,skiprows=54,
                names=names,header=0)


In [4]:
gooddata = data[data['f275w_mag'] != -99.9999]
gooddata = gooddata[gooddata['f336w_mag'] != -99.9999]
gooddata = gooddata[gooddata['f435w_mag'] != -99.9999]
gooddata = gooddata[gooddata['f606w_mag'] != -99.9999]
gooddata = gooddata[gooddata['f814w_mag'] != -99.9999]

In [5]:
# Takes a few seconds. 
catalog = SkyCoord(ra=gooddata['ra']*u.degree, dec=gooddata['dec']*u.degree)


In [6]:
rastar = 6.0324217 *u.deg
decstar = -72.0909325*u.deg
radiussearch = 1 * u.arcsec #arcsec






In [7]:
c = SkyCoord(ra=rastar,dec=decstar)
d2d = c.separation(catalog)
catalogmsk = d2d < radiussearch
idxcatalog = np.where(catalogmsk)[0]
print(len(idxcatalog))
annotation = ['a']*len(idxcatalog)

18


In [12]:
gooddata['separation_to_c_in_arcsec'] = d2d.arcsec
gooddata['separation_to_c'] = d2d

gooddata['color'] = 'green' 
gooddata['size'] = 1.

gooddata.loc[gooddata['separation_to_c'] < radiussearch.to(u.deg),'color'] = 'red'
gooddata.loc[gooddata['separation_to_c'] < radiussearch.to(u.deg),'size'] = 5


#color = np.array(color)
#dataclose = 
#datafar = daa[data['separation_to_c'] > radiussearch.to(u.deg)]

# Plot

In [13]:


xval = gooddata['f275w_mag']- gooddata['f336w_mag']

yval = gooddata['f275w_mag']


p = figure(plot_width=800, plot_height=500)
# change just some things about the x-axes
p.xaxis.axis_label = "275-336"


# change just some things about the y-axes
p.yaxis.axis_label = "275"


#f275 = np.array(f275)
#f336 = np.array(f336)




#Tool to get wavelength
hover2 = HoverTool(
        tooltips=[
            ("File index", "@name"),
            ('(ra,dec)', '(@ra,@dec)')
        ]
    )

        
p.add_tools(hover2)

source = ColumnDataSource(data=dict(
    x=xval,
    y=yval,
    color=gooddata['color'],
    size = gooddata['size'],
    ra = gooddata['ra'],
    dec = gooddata['dec'],
    name = gooddata['star_id']
))


# add a circle renderer with a size, color, and alpha
p.circle('x','y',color='color',size='size',source=source)

annotationx = xval[gooddata['separation_to_c'] < radiussearch.to(u.deg)]
annotationy = yval[gooddata['separation_to_c'] < radiussearch.to(u.deg)]
annotationtext = gooddata.loc[gooddata['separation_to_c'] < radiussearch.to(u.deg),'star_id']

p.text(annotationx, annotationy, annotationtext, angle=0.3, text_color="#96deb3")
#plot.add_glyph(source, glyph)



#p = Scatter(data, x=xval, y=yval, title=title, xlabel=xlabel, ylabel=ylabel)
xmax = xval.max()
xmin = xval.min()
ymax = yval.min()
ymin = yval.max()
p.x_range = Range1d(xmin, xmax)
p.y_range = Range1d(ymin, ymax)
show(p)

# Create Region

In [14]:
findreg = 'closestarsw21.reg'
gooddataclose = gooddata[gooddata['separation_to_c'] < radiussearch.to(u.deg)]
with open(findreg,'w') as fileone:
    for raa,decc,idstar in zip(gooddataclose['ra'],gooddataclose['dec'],gooddataclose['star_id']):
        text = f'fk5;circle({raa},{decc},0.1") # color=green text = {idstar}\n'
        fileone.write(text)
    

In [15]:
idstar

'R0082954'

In [16]:
! head closestarsw21.reg

fk5;circle(6.032671,-72.091096,0.1") # color=green text = R0005601
fk5;circle(6.033123000000001,-72.091091,0.1") # color=green text = R0005607
fk5;circle(6.0316980000000004,-72.090947,0.1") # color=green text = R0005680
fk5;circle(6.0324160000000004,-72.090786,0.1") # color=green text = R0005776
fk5;circle(6.032776999999999,-72.09076,0.1") # color=green text = R0005786
fk5;circle(6.0322379999999995,-72.090663,0.1") # color=green text = R0005827
fk5;circle(6.033004,-72.090997,0.1") # color=green text = R0082864
fk5;circle(6.032734,-72.091049,0.1") # color=green text = R0082865
fk5;circle(6.031855,-72.090829,0.1") # color=green text = R0082873
fk5;circle(6.032523,-72.09104599999999,0.1") # color=green text = R0082911


# ID R005776

In [17]:
for i in in gooddataclose.iloc:
    print(i)

SyntaxError: invalid syntax (<ipython-input-17-23b3417ed0dc>, line 1)

In [36]:
rstar1 = gooddataclose[gooddataclose['star_id'] == 'R0005776']
rstar1[['star_id','separation_to_c_in_arcsec','f275w_mag','f336w_mag','f435w_mag','f606w_mag','f814w_mag']]

star_id  separation_to_c_in_arcsec  f275w_mag  f336w_mag  f435w_mag  \
5757  R0005776                   0.527438    18.9137     17.048    16.7857   

      f606w_mag  f814w_mag  
5757     15.652    14.9244

In [31]:
rstar2 = gooddataclose[gooddataclose['star_id'] == 'R0005786']
rstar2[['star_id','separation_to_c_in_arcsec','f275w_mag','f336w_mag','f435w_mag','f606w_mag','f814w_mag']]

star_id  separation_to_c_in_arcsec  f275w_mag  f336w_mag  f435w_mag  \
5767  R0005786                   0.735084    16.6003    15.0458    14.7625   

      f606w_mag  f814w_mag  
5767    13.7891     13.123

In [32]:
rstar3 = gooddataclose[gooddataclose['star_id'] == 'R0082948']
rstar3[['star_id','separation_to_c_in_arcsec','f275w_mag','f336w_mag','f435w_mag','f606w_mag','f814w_mag']]

star_id  separation_to_c_in_arcsec  f275w_mag  f336w_mag  f435w_mag  \
82918  R0082948                   0.499186    20.7024    19.3543    19.4353   

       f606w_mag  f814w_mag  
82918     18.673    17.9564

In [33]:
19.3543 - 15.0458 

4.308499999999999

In [34]:
w21 = gooddataclose[gooddataclose['star_id'] == 'R0082912']
w21[['star_id','separation_to_c_in_arcsec','f275w_mag','f336w_mag','f435w_mag','f606w_mag','f814w_mag']]

star_id  separation_to_c_in_arcsec  f275w_mag  f336w_mag  f435w_mag  \
82882  R0082912                   0.030968    21.4878    20.9576    21.2883   

       f606w_mag  f814w_mag  
82882    20.7916    20.3207

In [35]:
20.9576 - 17.048 

3.909600000000001